<a href="https://colab.research.google.com/github/fbeilstein/machine_learning/blob/master/seminar_5_5_optimization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
print("Hello")

Hello


Explore gradient descent with the following code.
You should understand how it works and its weaknesses.
If you run out of ideas, use the following parameters

function_name | x_ini | y_ini | max_iter | theta | comment
---|---|---|---|---|---
```x**2 + y**2``` | -5.0 | -4.0 | 20 | 0.1 | good convex function
```sin(x) + sin(y)``` | 1.0 | 1.0 | 10 | 0.01 | many global minima
```(1-x**2)+100*(y-x**2)**2``` | -1.0 | -1.0 | 10 | 0.01 | famous Rosenbrock function

In [0]:
#@title # Exploring gradient+hessian descent

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

#@markdown ---
#@markdown ##Gradient descent options
#@markdown These variables correspond to the parameters of the minimizator
x_ini = 1.9 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

y_ini = 2.4 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

max_iter = 50 #@param {type:"slider", min:2, max:50, step:1}

#@markdown ---
#@markdown ##Function to minimize
#@markdown Write function using sympy syntax.
#@markdown Use x and y as variables.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html

function_name = 'x**2+(3*y)**2' #@param {type:"string"}

from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
Gx = diff(f, 'x')
Gy = diff(f, 'y')
g_xx = lambda x,y: diff(diff(f, 'x'), 'x').evalf(subs={'x':x, 'y':y})
g_xy = lambda x,y: diff(diff(f, 'x'), 'y').evalf(subs={'x':x, 'y':y})
g_yy = lambda x,y: diff(diff(f, 'y'), 'y').evalf(subs={'x':x, 'y':y})
H = lambda x,y: np.array([[g_xx(x, y), g_xy(x, y)], [g_xy(x, y), g_yy(x, y)]], dtype=float)

trace = [[x_ini, y_ini, f.evalf(subs={'x':x_ini, 'y':y_ini})]]
for i in range(max_iter):
  g_x = Gx.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  g_y = Gy.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  h = np.array([g_x, g_y])
  H_ = H(trace[-1][0], trace[-1][1])
  theta = np.dot(h, h) / np.dot(h, H_.dot(h))
  x_new = trace[-1][0] - theta * g_x
  y_new = trace[-1][1] - theta * g_y
  z_new = f.evalf(subs={'x':x_new, 'y':y_new})
  trace.append([x_new, y_new, z_new])
trace = np.array(trace, dtype=float)

x_min = min(-10.0, np.min(trace[:,0]))
x_max = max(10.0, np.max(trace[:,0]))
y_min = min(-10.0, np.min(trace[:,1]))
y_max = max(10.0, np.max(trace[:,1]))

# function calculated for 3d plot
x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[f.evalf(subs={'x':x__, 'y':y__}) for x__ in x_] for y__ in y_], dtype=float)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "xy"}]])

fig.add_trace(go.Scatter3d(x=trace[:, 0], y=trace[:, 1], z=trace[:, 2], 
                           marker=dict(size=4, colorscale='Viridis'),
                           line=dict(color='red', width=2)),
              row=1, col=1)

fig.add_trace(go.Surface(x=x_, y=y_, z=z_, opacity=0.9, showscale=False),
              row=1, col=1)

fig.add_trace(go.Contour(z=z_, x=x_, y=y_, contours=dict(showlabels=True)),
              row=1, col=2)

fig.add_trace(go.Scatter(x=trace[:, 0], y=trace[:, 1], line=dict(color='red', width=2)),
              row=1, col=2)

fig.update_layout(width=1200, height=600, autosize=False, 
                  title_text="Gradient descent demonstration",
                  #scene=dict(aspectratio = dict(x=1, y=1, z=1)),
                  showlegend=False)
fig.show()

In [0]:
#@title # Exploring Newton's method

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

#@markdown ---
#@markdown ##Gradient descent options
#@markdown These variables correspond to the parameters of the minimizator
x_ini = 1.9 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

y_ini = 2.4 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

max_iter = 50 #@param {type:"slider", min:2, max:50, step:1}

#@markdown ---
#@markdown ##Function to minimize
#@markdown Write function using sympy syntax.
#@markdown Use x and y as variables.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html

function_name = 'x**2+(3*y)**2+sin(x)' #@param {type:"string"}

from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
Gx = diff(f, 'x')
Gy = diff(f, 'y')
g_xx = lambda x,y: diff(diff(f, 'x'), 'x').evalf(subs={'x':x, 'y':y})
g_xy = lambda x,y: diff(diff(f, 'x'), 'y').evalf(subs={'x':x, 'y':y})
g_yy = lambda x,y: diff(diff(f, 'y'), 'y').evalf(subs={'x':x, 'y':y})
H = lambda x,y: np.array([[g_xx(x, y), g_xy(x, y)], [g_xy(x, y), g_yy(x, y)]], dtype=float)

trace = [[x_ini, y_ini, f.evalf(subs={'x':x_ini, 'y':y_ini})]]
for i in range(max_iter):
  g_x = Gx.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  g_y = Gy.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  h = np.array([g_x, g_y])
  H_ = H(trace[-1][0], trace[-1][1])
  H_inv = np.linalg.inv(H_)
  theta = H_inv.dot(h)
  x_new = trace[-1][0] - theta[0]
  y_new = trace[-1][1] - theta[1]
  z_new = f.evalf(subs={'x':x_new, 'y':y_new})
  trace.append([x_new, y_new, z_new])
trace = np.array(trace, dtype=float)

x_min = min(-10.0, np.min(trace[:,0]))
x_max = max(10.0, np.max(trace[:,0]))
y_min = min(-10.0, np.min(trace[:,1]))
y_max = max(10.0, np.max(trace[:,1]))

# function calculated for 3d plot
x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[f.evalf(subs={'x':x__, 'y':y__}) for x__ in x_] for y__ in y_], dtype=float)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "xy"}]])

fig.add_trace(go.Scatter3d(x=trace[:, 0], y=trace[:, 1], z=trace[:, 2], 
                           marker=dict(size=4, colorscale='Viridis'),
                           line=dict(color='red', width=2)),
              row=1, col=1)

fig.add_trace(go.Surface(x=x_, y=y_, z=z_, opacity=0.9, showscale=False),
              row=1, col=1)

fig.add_trace(go.Contour(z=z_, x=x_, y=y_, contours=dict(showlabels=True)),
              row=1, col=2)

fig.add_trace(go.Scatter(x=trace[:, 0], y=trace[:, 1], line=dict(color='red', width=2)),
              row=1, col=2)

fig.update_layout(width=1200, height=600, autosize=False, 
                  title_text="Gradient descent demonstration",
                  #scene=dict(aspectratio = dict(x=1, y=1, z=1)),
                  showlegend=False)
fig.show()

In [0]:
#@title # Exploring simple gradient descent

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

#@markdown ---
#@markdown ##Gradient descent options
#@markdown These variables correspond to the parameters of the minimizator
x_ini = 7.6 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

y_ini = 1.7 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

max_iter = 50 #@param {type:"slider", min:2, max:50, step:1}

theta = 0.477 #@param {type:"slider", min:0, max:1, step:0.001}
#@markdown ---
#@markdown ##Function to minimize
#@markdown Write function using sympy syntax.
#@markdown Use x and y as variables.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html

function_name = 'x**2+(3*y)**2' #@param {type:"string"}

from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
Gx = diff(f, 'x')
Gy = diff(f, 'y')

trace = [[x_ini, y_ini, f.evalf(subs={'x':x_ini, 'y':y_ini})]]
for i in range(max_iter):
  g_x = Gx.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  g_y = Gy.evalf(subs={'x':trace[-1][0], 'y':trace[-1][1]})
  x_new = trace[-1][0] - theta * g_x
  y_new = trace[-1][1] - theta * g_y
  z_new = f.evalf(subs={'x':x_new, 'y':y_new})
  trace.append([x_new, y_new, z_new])
trace = np.array(trace, dtype=float)

x_min = min(-10.0, np.min(trace[:,0]))
x_max = max(10.0, np.max(trace[:,0]))
y_min = min(-10.0, np.min(trace[:,1]))
y_max = max(10.0, np.max(trace[:,1]))

# function calculated for 3d plot
x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[f.evalf(subs={'x':x__, 'y':y__}) for x__ in x_] for y__ in y_], dtype=float)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "xy"}]])

fig.add_trace(go.Scatter3d(x=trace[:, 0], y=trace[:, 1], z=trace[:, 2], 
                           marker=dict(size=4, colorscale='Viridis'),
                           line=dict(color='red', width=2)),
              row=1, col=1)

fig.add_trace(go.Surface(x=x_, y=y_, z=z_, opacity=0.9, showscale=False),
              row=1, col=1)

fig.add_trace(go.Contour(z=z_, x=x_, y=y_, contours=dict(showlabels=True)),
              row=1, col=2)

fig.add_trace(go.Scatter(x=trace[:, 0], y=trace[:, 1], line=dict(color='red', width=2)),
              row=1, col=2)

fig.update_layout(width=1200, height=600, autosize=False, 
                  title_text="Gradient descent demonstration",
                  #scene=dict(aspectratio = dict(x=1, y=1, z=1)),
                  showlegend=False)
fig.show()

In [0]:
#@title # Exploring minimization methods

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np
from scipy.optimize import minimize

#@markdown ---
#@markdown ##Minimization options
#@markdown These variables correspond to the parameters of the minimizator
x_ini = -7.1 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}
y_ini = -3.6 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}


method = 'Nelder-Mead' #@param ['Nelder-Mead','Powell','CG','BFGS','Newton-CG','L-BFGS-B','TNC','COBYLA','SLSQP','trust-constr','dogleg','trust-ncg','trust-exact','trust-krylov']

max_iter = 50 #@param {type:"slider", min:2, max:50, step:1}

jacobian = 'none' #@param ['none', '2-point', '3-point', 'cs', 'custom']

hessian = 'none' #@param ['none', '2-point', '3-point', 'cs', 'custom']

#@markdown ---
#@markdown ##Function to minimize
#@markdown Write function using sympy syntax.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html


function_name = 'x**2+(3*y)**2' #@param {type:"string"}


from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
g_x = lambda x,y: diff(f, 'x').evalf(subs={'x':x, 'y':y})
g_y = lambda x,y: diff(f, 'y').evalf(subs={'x':x, 'y':y})

if jacobian == 'custom':
  jacobian = lambda x: np.array([g_x(x[0], x[1]), g_y(x[0], x[1])], dtype=float)
if jacobian == 'none':
  jacobian = None

g_xx = lambda x,y: diff(diff(f, 'x'), 'x').evalf(subs={'x':x, 'y':y})
g_xy = lambda x,y: diff(diff(f, 'x'), 'y').evalf(subs={'x':x, 'y':y})
g_yy = lambda x,y: diff(diff(f, 'y'), 'y').evalf(subs={'x':x, 'y':y})
H = lambda x,y: [[g_xx(x, y), g_xy(x, y)], [g_xy(x, y), g_yy(x, y)]]

if hessian == 'custom':
  hessian = lambda x: np.array(H(x[0], x[1]), dtype=float)
if hessian == 'none':
  hessian = None


func_to_minimize = lambda x: f.evalf(subs={'x':x[0], 'y':x[1]})
history = [np.array([x_ini, y_ini])]
store_data = lambda xk : history.append(xk)

minimize(func_to_minimize, [x_ini, y_ini], 
         method=method, jac=jacobian, hess=hessian,
         options={'maxiter':max_iter}, callback=store_data)

_h = np.array(history)
_x = _h.T[0]
_y = _h.T[1]
_z = np.array([func_to_minimize(x) for x in history], dtype=float)

x_min = min(-10.0, np.min(_x))
x_max = max(10.0, np.max(_x))
y_min = min(-10.0, np.min(_y))
y_max = max(10.0, np.max(_y))

x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[func_to_minimize([x,y]) for x in x_] for y in y_], dtype=float)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "xy"}]])

fig.add_trace(go.Scatter3d(x=_x, y=_y, z=_z, marker=dict(size=4, colorscale='Viridis'),
                                             line=dict(color='red', width=2)),
              row=1, col=1)

fig.add_trace(go.Surface(x=x_, y=y_, z=z_, opacity=0.9, showscale=False),
              row=1, col=1)

fig.add_trace(go.Contour(z=z_, x=x_, y=y_, contours=dict(showlabels=True)),
              row=1, col=2)

fig.add_trace(go.Scatter(x=_x, y=_y, line=dict(color='red', width=2)),
              row=1, col=2)

fig.update_layout(width=1200, height=600, autosize=False, 
                  title_text="Optimization demonstration",
                  scene=dict(aspectratio = dict(x=1, y=1, z=1)),
                  showlegend=False)
fig.show()

In [0]:
#@title # [Very experimental code] Exploring minimization methods

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np
from scipy.optimize import minimize

#@markdown ---
#@markdown ##Minimization options
#@markdown These variables correspond to the parameters of the minimizator
x_ini = -7.1 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}
y_ini = -3.6 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}


method = 'Nelder-Mead' #@param ['Nelder-Mead','Powell','CG','BFGS','Newton-CG','L-BFGS-B','TNC','COBYLA','SLSQP','trust-constr','dogleg','trust-ncg','trust-exact','trust-krylov']

max_iter = 20 #@param {type:"slider", min:2, max:50, step:1}

jacobian = 'none' #@param ['none', '2-point', '3-point', 'cs', 'custom']

hessian = 'none' #@param ['none', '2-point', '3-point', 'cs', 'custom']

#@markdown ---
#@markdown ##Function to minimize
#@markdown Write function using sympy syntax.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html


function_name = 'x**2+(3*y)**2' #@param {type:"string"}


from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
g_x = lambda x,y: diff(f, 'x').evalf(subs={'x':x, 'y':y})
g_y = lambda x,y: diff(f, 'y').evalf(subs={'x':x, 'y':y})

if jacobian == 'custom':
  jacobian = lambda x: np.array([g_x(x[0], x[1]), g_y(x[0], x[1])], dtype=float)
if jacobian == 'none':
  jacobian = None

g_xx = lambda x,y: diff(diff(f, 'x'), 'x').evalf(subs={'x':x, 'y':y})
g_xy = lambda x,y: diff(diff(f, 'x'), 'y').evalf(subs={'x':x, 'y':y})
g_yy = lambda x,y: diff(diff(f, 'y'), 'y').evalf(subs={'x':x, 'y':y})
H = lambda x,y: [[g_xx(x, y), g_xy(x, y)], [g_xy(x, y), g_yy(x, y)]]

if hessian == 'custom':
  hessian = lambda x: np.array(H(x[0], x[1]), dtype=float)
if hessian == 'none':
  hessian = None


func_to_minimize = lambda x: f.evalf(subs={'x':x[0], 'y':x[1]})
history = [np.array([x_ini, y_ini])]
store_data = lambda xk : history.append(xk)

minimize(func_to_minimize, [x_ini, y_ini], 
         method=method, jac=jacobian, hess=hessian,
         options={'maxiter':max_iter}, callback=store_data)

_h = np.array(history)
_x = _h.T[0]
_y = _h.T[1]
_z = np.array([func_to_minimize(x) for x in history], dtype=float)

x_min = min(-10.0, np.min(_x))
x_max = max(10.0, np.max(_x))
y_min = min(-10.0, np.min(_y))
y_max = max(10.0, np.max(_y))

x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[func_to_minimize([x,y]) for x in x_] for y in y_], dtype=float)

fig = dict(
    layout = dict(
        width=1200, height=600, autosize=False,
        showlegend = False,
        scene = { 'domain': { 'x': [0.0, 0.44], 'y': [0, 1] } },
        xaxis1 = {'domain': [0.55, 1]},
        yaxis1 = {'domain': [0.0, 1.0]},
        title  = 'Minimization',
        margin = {'t': 50, 'b': 50, 'l': 50, 'r': 50},
        updatemenus = [{'buttons': [{'args': [[k for k in range(len(_h)-1)],
                                              {'frame': {'duration': 500.0, 'redraw': True},
                                               'fromcurrent': False, 'transition': {'duration': 0, 'easing': 'linear'}}],
                                     'label': 'Play',
                                     'method': 'animate'},
                                    {'args': [[None], {'frame': {'duration': 0, 'redraw': True},
                                                       'mode': 'immediate',
                                                       'transition': {'duration': 0}}
                                              ],
                                     'label': 'Pause',
                                     'method': 'animate'
                                     }
                                    ],
                        'direction': 'left',
                        'pad': {'r': 10, 't': 85},
                        'showactive': True,
                        'type': 'buttons', 'x': 0.1, 'y': 0, 'xanchor': 'right', 'yanchor': 'top'}],
        sliders = [{'yanchor': 'top',
                    'xanchor': 'left',
                    'currentvalue': {'font': {'size': 16}, 'prefix': 'Step: ', 'visible': True, 'xanchor': 'right'},
                    'transition': {'duration': 0.0},
                    'pad': {'b': 10, 't': 50},
                    'len': 0.9,
                    'x': 0.1,
                    'y': 0,
                    'steps': [{'args': [[k], {'frame': {'duration': 500.0, 'easing': 'linear', 'redraw': True},
                                              'transition': {'duration': 0, 'easing': 'linear'}}
                                        ],
                               'label': k,
                               'method': 'animate'} for k in range(len(_h)-1)
                    ]}]
    ),
    data = [
        {'type': 'scatter3d', 'name': 's3', 'x': _x, 'y': _y, 'z': _z, 'line': {'color': 'red', 'width': 2}, 'marker': {'size': 4, 'colorscale': 'Viridis'}},
        {'type': 'surface', 'name': 'f2', 'x': x_, 'y': y_, 'z': z_, 'opacity': 0.8, 'showscale': False},
        {'type': 'contour', 'name': 'c1', 'x':x_, 'y':y_, 'z':z_, 'contours': {'showlabels': True}},
        {'type': 'scatter', 'name': 's2', 'x': _x, 'y': _y, 'line': {'color': 'red', 'width': 2}}
    ],
    frames=[
        {'name': str(k),
         'data': [
          {'type': 'scatter3d', 'name': 's3', 'x': _x[:k], 'y': _y[:k], 'z': _z[:k], 'line': {'color': 'red', 'width': 2}, 'marker': {'size': 4, 'colorscale': 'Viridis'}},
          {'type': 'surface', 'name': 'f2', 'x': x_, 'y': y_, 'z': z_, 'opacity': 0.8, 'showscale': False},
          {'type': 'contour', 'name': 'c1', 'x':x_, 'y':y_, 'z':z_, 'contours': {'showlabels': True}},
          {'type': 'scatter', 'name': 's2', 'x': _x[:k], 'y': _y[:k], 'line': {'color': 'red', 'width': 2}}
         ]} for k in range(len(_h)-1) ]
)
#plot(fig, auto_open=False)
f = go.Figure(fig)
f.show()

In [68]:
#@title # [Very experimental code] Exploring function slices

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np
from scipy.optimize import minimize

#@markdown ---
#@markdown ##Minimization options
#@markdown These variables correspond to the point through which rotation axis passes
x_ini = -1.1 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}
y_ini = 1.6 #@param {type:"slider", min:-10.0, max:10.0, step:0.1}

#@markdown ---
#@markdown ##Function to explore
#@markdown Write function using sympy syntax.
#@markdown You can use all elementary functions, (inverse)trigonometric, (inverse)hyperbolic functions, etc.
#@markdown for more details visit http://www.cfm.brown.edu/people/dobrush/am33/SymPy/function.html


function_name = 'x**2+(3*y)**2' #@param {type:"string"}


from sympy.parsing.sympy_parser import standard_transformations, implicit_multiplication_application, parse_expr
transformations = (standard_transformations + (implicit_multiplication_application,))
f = parse_expr(function_name, transformations=transformations)

from sympy import diff
g_x = lambda x,y: diff(f, 'x').evalf(subs={'x':x, 'y':y})
g_y = lambda x,y: diff(f, 'y').evalf(subs={'x':x, 'y':y})
jacobian = lambda x: np.array([g_x(x[0], x[1]), g_y(x[0], x[1])], dtype=float)

g_xx = lambda x,y: diff(diff(f, 'x'), 'x').evalf(subs={'x':x, 'y':y})
g_xy = lambda x,y: diff(diff(f, 'x'), 'y').evalf(subs={'x':x, 'y':y})
g_yy = lambda x,y: diff(diff(f, 'y'), 'y').evalf(subs={'x':x, 'y':y})
H = lambda x,y: [[g_xx(x, y), g_xy(x, y)], [g_xy(x, y), g_yy(x, y)]]
hessian = lambda x: np.array(H(x[0], x[1]), dtype=float)


func_to_minimize = lambda x: f.evalf(subs={'x':x[0], 'y':x[1]})
history = [np.array([x_ini, y_ini])]
store_data = lambda xk : history.append(xk)


x_min = -10.0
x_max =  10.0
y_min = -10.0
y_max =  10.0

x_ = np.linspace(x_min, x_max, num=50)
y_ = np.linspace(y_min, y_max, num=50)
z_ = np.array([[func_to_minimize([x,y]) for x in x_] for y in y_], dtype=float)

z_max = np.max(z_)
z_min = np.min(z_)

in_square = lambda p, v: x_min < p * v[0] + x_ini< x_max and y_min < p * v[1] + y_ini < y_max

def slice_XY(angle):
  param = np.linspace(-np.sqrt((x_max-x_min)**2 + (y_max-y_min)**2), 
                      +np.sqrt((x_max-x_min)**2 + (y_max-y_min)**2), 
                      50)
  vec = np.array([np.cos(angle / 180.0 * np.pi), np.sin(angle / 180.0 * np.pi)])
  in_s = lambda p: in_square(p, vec)
  return np.array([[p * vec[0] + x_ini, p * vec[1] + y_ini, p] 
                    for p in filter(in_s, param)], dtype=float)

def slice(angle):
  xy_coords = slice_XY(angle)
  return np.array([[p[0], p[1], func_to_minimize(p[:2]), p[2]] for p in xy_coords], dtype=float)

def plane(angle):
  xy = slice_XY(angle)
  return np.array([[xy[0,0], xy[0,1], z_min], 
                   [xy[0,0], xy[0,1], z_max],
                   [xy[-1,0], xy[-1,1], z_max], 
                   [xy[-1,0], xy[-1,1], z_min],
                   [x_ini, y_ini, z_min]], dtype=float)

def plot_data(angle):
  return [{'type': 'scatter3d', 'mode': 'lines', 'name': 's3', 'x': slice(angle)[:,0], 'y': slice(angle)[:,1], 'z': slice(angle)[:,2], 'line': {'color': 'red', 'width': 2}},
          {'type': 'surface', 'name': 'f2', 'x': x_, 'y': y_, 'z': z_, 'opacity': 0.8, 'showscale': False},
          {'type': 'mesh3d', 'name': 'f2', 'alphahull':0, 'x': plane(angle)[:,0], 'y': plane(angle)[:,1], 'z': plane(angle)[:,2], 'color':'blue', 'opacity': 0.6, 'showscale': False},
          {'type': 'scatter3d', 'mode': 'lines', 'name': 's3', 'x': [x_ini, x_ini], 'y': [y_ini, y_ini], 'z': [z_min, z_max], 'line': {'color': 'green', 'width': 2}},
          {'type': 'scatter', 'name': 's2', 'x': slice(angle)[:,3], 'y': slice(angle)[:,2], 'line': {'color': 'blue', 'width': 2}}
         ]

fig = dict(
    layout = dict(
        width=1200, height=600, autosize=False,
        showlegend = False,
        scene = { 'domain': { 'x': [0.0, 0.44], 'y': [0, 1] } },
        xaxis1 = {'domain': [0.55, 1]},
        yaxis1 = {'domain': [0.0, 1.0]},
        title  = 'Minimization',
        margin = {'t': 50, 'b': 50, 'l': 50, 'r': 50},
        sliders = [{'yanchor': 'top',
                    'xanchor': 'left',
                    'currentvalue': {'font': {'size': 16}, 
                                     'prefix': 'Angle: ', 
                                     'visible': True, 
                                     'xanchor': 'right'},
                    'transition': {'duration': 0.0},
                    'pad': {'b': 10, 't': 50},
                    'len': 0.9,
                    'x': 0.1,
                    'y': 0,
                    'steps': [{'args': [[k], {'frame': 
                                              {'duration': 0.0, 
                                               'easing': 'linear', 
                                               'redraw': True},
                                              'transition': 
                                              {'duration': 0, 
                                               'easing': 'linear'
                                               }
                                              }
                                        ],
                               'label': k * 5.0,
                               'method': 'animate'} for k in range(36)
                    ]}]
    ),
    data = plot_data(0.01),
    frames=[
        {'name': k,
         'data': plot_data(5.0 * k + 0.01)} for k in range(36) ]
)
#plot(fig, auto_open=False)
f = go.Figure(fig)
f.show()